# Exercise 2

## Lossless Data Compression: Rice Coding

<p style="font-size:15px">In this exercise, we will be implementing a lossless data compression application based on rice coding. We will take two different audio files and encode them. The application should also be able to decode and create a "new" decompressed audio file which can be played back.</p>

<p style="font-size:15px;">Let's take a listen to the sounds.</p>

In [1]:
pip install numpy

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install wave

  Created wheel for wave: filename=Wave-0.0.2-py3-none-any.whl size=1245 sha256=8998e865a466a0f0d682d0bf566c8259f15d07c9fe924220dc43dc962987b887
  Stored in directory: /home/jovyan/.cache/pip/wheels/25/e8/fe/458c7dac00c6abedad6380b9d0ef1a5cbc7c21807df1d30915
Successfully built wave
You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [3]:
pip install soundfile

You should consider upgrading via the '/opt/conda/bin/python -m pip install --upgrade pip' command.
Note: you may need to restart the kernel to use updated packages.


In [4]:
import numpy as np
import wave
import IPython.display as ipd
import soundfile as sf

In [5]:
ipd.Audio("Exercise2_Files/Sound1.wav")

In [6]:
ipd.Audio("Exercise2_Files/Sound2.wav")

<p style="font-size:15px;">Let's also extract information about the audio file. The <strong>get_info</strong> function will print the sample rate, number of channels, subtype, shape and samples of the audio file.</p>

In [7]:
def get_info(file):
    sound = sf.SoundFile(file)
    print('Sample rate: {}'.format(sound.samplerate))
    print('Channels: {}'.format(sound.channels))
    print('Subtype: {}'.format(sound.subtype))

    sample, fs = sf.read(file, dtype='int16')
    print("Shape:", np.shape(sample))
    print("Samples:", sample)
    print(type(sample))

In [8]:
get_info("Exercise2_Files/Sound1.wav")

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (501022,)
Samples: [-7 -7 -7 ...  0  2  1]
<class 'numpy.ndarray'>


In [9]:
get_info("Exercise2_Files/Sound2.wav")

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (504000,)
Samples: [ -999   886 -1325 ...    31  -876   339]
<class 'numpy.ndarray'>


## Encoding

<p style="font-size:15px;">Let's look at how the rice encoding algorithm works.</p>

1. Fix an integer value K.
2. Compute the modulus, M by using the equation $ M = 2^K $
3. For S, the number to be encoded, find
    1. quotient = $ q = int(S/M) $
    2. remainder = $ r = S  modulo  M $
4. Generate Codeword
    1. The Quotient_Code is q in unary format.
    2. The Remainder_Code is r in binary using K bits.
    3. The Codeword will have the format <Quotient_Code\> <Remainder_Code\>
    
<p style="font-size:15px;">Using the instructions, the below function <strong>encode_bytes</strong> automates the algorithm.</p><p style="font-size:14px; color:red;">The function will contain comments to explain the code more in-depth.</p>
<p hidden>if limit >= 3296 and limit <= 3300:</p>

In [10]:
def bitstring_to_bytes(s):
    return int(s, 2).to_bytes((len(s) + 7) // 8, byteorder='big')

def encode(file, k):
    # open the given file
    sound = wave.open(file, mode='rb')
    # extract unsigned samples from the sound file
    data = bytearray(list(sound.readframes(sound.getnframes())))
    # get sound parameters - this will be returned and used in the decoding function
    params = sound.getparams()
    
    # open new file for writing
    temp = file.split('.')
    writefile = temp[0] + "_" + str(k) + "bit_Enc" + ".ex2"
    f = open(writefile, 'wb')
    
    # loop through the data
    # s is the sample (number) to be encoded
    for s in data:
        # m is 2 to the power of k (bits)
        m = 2**k
        # find the quotient of s divided by m
        q = int(s/m)
        # find the remainder of s divided by m
        r = s % m
        
        # to generate the quotient code, the code will loop according to range(q)
        # during each loop, "1" will be incremently added to the string
        quotient = ""
        for _ in range(q):
            quotient += "1"
        # you will see here that i have done away with adding a "0" at the end of quotient
        # this will be explained in the decoding function
#         # at the end, add "0"
#         quotient += "0"

        # to generate the remainder code, first convert the integer to binary
        remainder = bin(r)
        # drop the two first values "0b" to make the binary into a k-bit binary
        remainder = remainder[2:]
        
        # in the case that the binary code has insignificant 0's i.e. 0011 will be converted to 11 from it's int (4-bit)
        # loop and add the 0's back at the start
        if len(remainder) < (k+1):
            for _ in range(k-len(remainder)):
                remainder = "0" + remainder
                
        # combine quotient + remainder to generate final code
        code = quotient + remainder
        # convert the bit string into bytes for storing
        byte_code = bitstring_to_bytes(code)
        # calculate the length of the byte for storing - explained in decoding function
        length = bitstring_to_bytes(bin(len(byte_code))[2:])

        # IMPORTANT - write LENGTH before BYTE
        f.write(length)
        f.write(byte_code)
            
    sound.close()
    f.close()
    print("Encoding complete.")
    return writefile, params

## Decoding

<p style="font-size:15px;">The way to decode goes as such:</p>

1. Determine q by counting the number of 1s before the first 0.
2. Determine r reading the next K bits as a binary value.
3. Write out S, the encoded number, as q × M + r.

<p style="font-size:14px; color:red;">The function will contain comments to explain the code more in-depth.</p>

In [11]:
def decode(file, k, params):
    # initialize a new empty list - this will be used to write the samples into a new wavfile
    decoded_data = []
    
    # open the given file
    f = open(file, 'rb')
    # in the encoding function, we first wrote in the length of the byte_code in byte
    # f.read(1) reads only ONE byte
    # hence the integer derived from first byte will be the next number of bytes to read to determine s
    length = f.read(1)
    # while length is True
    while length:
        # get the integer from length
        length = int.from_bytes(length, "big")
        # now read the next bytes to get the byte_code
        byte_code = f.read(length)
        # as always, m is 2 to the power of k
        m = 2**k
        
        # generate the bit string from byte
        code = ''.join(format(b, '08b') for b in byte_code)
        # in the encoding function, i mentioned that i did away with adding "0" as the last bit in quotient
        # the reason for this is that i am able to get the remainder by extracting the last k values
        # from the bit string itself without looking for the first 0 and vice versa for quotient
        quotient = code[:(len(code)-k)]
        remainder = code[(len(code)-k):]
        
        # to calculate q, loop through quotient and increment q by 1 if each char is "1"
        q = 0
        for _ in quotient:
            if _ == '1':
                q += 1
        # calculate r by converting the string to int
        if remainder != '':
            r = int(remainder, 2)
        # finally, calculate s
        s = (q * m) + r
        
        # append s into the new list
        decoded_data.append(s)
        # read the next ONE byte (length of next byte to be read)
        length = f.read(1)

    # open new wavfile
    temp = file.split(".")
    writefile = temp[0] + "_Dec.wav"  
    with wave.open(writefile, 'wb') as fd:
        # set parameters
        fd.setparams(params)
        # convert list to bytes and write frames
        fd.writeframes(bytes(decoded_data))

    print("Decoding complete.")
    return writefile

## Compressing with K = 2 bits

<p style="font-size:15px;">Let's invoke the function on Sound 1. Remember that <strong>encode_bytes</strong> function takes in the filename of the audio file and number of bits and returns the encode filename and parameters to be passed into the <strong>decode_bytes</strong> function.</p>

In [12]:
sound1_2_encoded_file, sound1_2_params = encode("Exercise2_Files/Sound1.wav", 2)

Encoding complete.


<p style="font-size:15px;">Great, the encoding has been completed. Now let's decode the encoded file. We pass in the filename, number of bits and parameters into the decoding function. A <i>new</i> wavfile will be returned.</p>

In [13]:
sound1_2_decoded_file = decode(sound1_2_encoded_file, 2, sound1_2_params)

Decoding complete.


<p style="font-size:15px;">Let's listen to the new file.</p>

In [14]:
ipd.Audio(sound1_2_decoded_file)

<p style="font-size:15px;">Let's also get information on the new wavfile to verify that the file has not been corrupted.</p>

In [15]:
get_info(sound1_2_decoded_file)

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (501022,)
Samples: [-7 -7 -7 ...  0  2  1]
<class 'numpy.ndarray'>


<p style="font-size:15px;">Success! The new wavfile sounds exactly the same as the original with no noise, and is not corrupted. Let's repeat on Sound 2.</p>

In [16]:
sound2_2_encoded_file, sound2_2_params = encode("Exercise2_Files/Sound2.wav", 2)

Encoding complete.


In [17]:
sound2_2_decoded_file = decode(sound2_2_encoded_file, 2, sound2_2_params)

Decoding complete.


In [18]:
ipd.Audio(sound2_2_decoded_file)

In [19]:
get_info(sound2_2_decoded_file)

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (504000,)
Samples: [ -999   886 -1325 ...    31  -876   339]
<class 'numpy.ndarray'>


<p style="font-size:15px;">Here are the sizes of the encoded files using K = 2 bits.</p>
<table>
  <tr>
    <th>Sound File</th>
    <th>K</th>
    <th>Size of *.ex2 file</th>
  </tr>
  <tr>
    <td>Sound1.wav</td>
    <td>2</td>
    <td>5.6 MB</td>
  </tr>
  <tr>
    <td>Sound2.wav</td>
    <td>2</td>
    <td>5.69 MB</td>
  </tr>
</table>

## Compressing with K = 4 bits

<p style="font-size:15px;">You'll notice that the sizes of the encoded files when using 2 bits is quite high. Let's try invoking the same functions, but this time using 4 bits and see if the size of the files are reduced.</p>

In [20]:
sound1_4_encoded_file, sound1_4_params = encode("Exercise2_Files/Sound1.wav", 4)

Encoding complete.


In [21]:
sound1_4_decoded_file = decode(sound1_4_encoded_file, 4, sound1_4_params)

Decoding complete.


In [22]:
ipd.Audio(sound1_4_decoded_file)

In [23]:
get_info(sound1_4_decoded_file)

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (501022,)
Samples: [-7 -7 -7 ...  0  2  1]
<class 'numpy.ndarray'>


In [24]:
sound2_4_encoded_file, sound2_4_params = encode("Exercise2_Files/Sound2.wav", 4)

Encoding complete.


In [25]:
sound2_4_decoded_file = decode(sound2_4_encoded_file, 4, sound2_4_params)

Decoding complete.


In [26]:
ipd.Audio(sound2_4_decoded_file)

In [27]:
get_info(sound2_4_decoded_file)

Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (504000,)
Samples: [ -999   886 -1325 ...    31  -876   339]
<class 'numpy.ndarray'>


<p style="font-size:15px;">Here are the sizes of the encoded files using K = 4 bits.</p>
<table>
  <tr>
    <th>Sound File</th>
    <th>K</th>
    <th>Size of *.ex2 file</th>
  </tr>
  <tr>
    <td>Sound1.wav</td>
    <td>4</td>
    <td>2.92 MB</td>
  </tr>
  <tr>
    <td>Sound2.wav</td>
    <td>4</td>
    <td>2.94 MB</td>
  </tr>
</table>

## Rice Coding: Conclusion

<p style="font-size:15px;">Rice coding can be a good algorithm, however, not for large samples where Q will be a large number. Since a string of "1" is added for every Q, should Q be a large number, a large Quotient code will be generated, which increases encoded file sizes greatly, especially for smaller K bits. One way to reduce this is to use <strong>larger bits</strong> such as 8 bits.</p>

In [28]:
sound1_8_encoded_file, sound1_8_params = encode("Exercise2_Files/Sound1.wav", 8)
sound1_8_decoded_file = decode(sound1_8_encoded_file, 8, sound1_8_params)
get_info(sound1_8_decoded_file)

Encoding complete.
Decoding complete.
Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (501022,)
Samples: [-7 -7 -7 ...  0  2  1]
<class 'numpy.ndarray'>


In [29]:
sound2_8_encoded_file, sound2_8_params = encode("Exercise2_Files/Sound2.wav", 8)
sound2_8_decoded_file = decode(sound2_8_encoded_file, 8, sound2_8_params)
get_info(sound2_8_decoded_file)

Encoding complete.
Decoding complete.
Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (504000,)
Samples: [ -999   886 -1325 ...    31  -876   339]
<class 'numpy.ndarray'>


<p style="font-size:15px;">The sizes of the encoded files are as follows:</p>
<table>
  <tr>
    <th>Sound File</th>
    <th>K</th>
    <th>Size of *.ex2 file</th>
  </tr>
  <tr>
    <td>Sound1.wav</td>
    <td>8</td>
    <td>2 MB</td>
  </tr>
  <tr>
    <td>Sound2.wav</td>
    <td>8</td>
    <td>2.02 MB</td>
  </tr>
</table>

<p style="font-size:15px;">Alternatively, since the value of Q can genrally be quite big, Q can be made smaller by halving it. Functions <strong>improved_code</strong> and <strong>improved_decode</strong> implements this.</p>

<p style="font-size:14px; color:red;">The functions will contain comments to explain the code more in-depth.</p>

In [30]:
def improved_encode(file, k):
    sound = wave.open(file, mode='rb')
    data = bytearray(list(sound.readframes(sound.getnframes())))
    params = sound.getparams()
    temp = file.split('.')
    writefile = temp[0] + "_" + str(k) + "bit_Enc_IMPROVED" + ".ex2"
    f = open(writefile, 'wb')
    
    for i in data:
        s = i
        m = 2**k
        q = int(s/m)
        r = s % m
        # instead of using q, which can be quite large, we will halve it instead
        quotient = ""
        # first we initialize a global variable "odd". This will be used to determine whether q is odd or even
        odd = False
        # check if q is odd
        if (q % 2) != 0:
            # set odd to True
            odd = True
            # add 1 to q to make it even and store into q_temp. q_temp will be used as the "new" q
            q_temp = q + 1
            # halve q_temp
            q_temp = int(q_temp/2)
        else:
            # if q is even, halve it automatically
            q_temp = int(q/2)
        # loop for range(q_temp) and add "1" to quotient each time
        for _ in range(q_temp):
            quotient += "1"
        # if odd is True, add a "0" at the end of quotient
        # this bit will be used in the decoding function to determine whether q is odd or even
        if odd == True:
            quotient += "0"
        # if odd is False, add a "1" at the end of quotient
        # this bit will be used in the decoding function to determine whether q is odd or even
        if odd == False:
            quotient += "1"
            
        remainder = bin(r)
        remainder = remainder[2:]
        if len(remainder) < (k+1):
            for _ in range(k-len(remainder)):
                remainder = "0" + remainder
                
        code = quotient + remainder
        byte = bitstring_to_bytes(code)
        length = bitstring_to_bytes(bin(len(byte))[2:])

        f.write(length)
        f.write(byte)
            
    sound.close()
    f.close()
    print("Encoding complete.")
    return writefile, params

def improved_decode(file, k, params):
    decoded_data = []
    
    f = open(file, 'rb')
    length = f.read(1)
    while length:
        length = int.from_bytes(length, "big")
        i = f.read(length)
        
        m = 2**k
        code = ''.join(format(b, '08b') for b in i)
        # this quotient contains the last bit that will determine whether q is odd or even
        quotient = code[:(len(code)-k)]
        remainder = code[(len(code)-k):]
        
        # get the last bit
        sign = quotient[len(quotient)-1:]
        # get the rest of quotient
        quotient = quotient[:len(quotient)-1]
        
        q_temp = 0
        odd = False
        # if sign is 0, set odd to True
        if sign == "0":
            odd = True
        # increment q_temp for each "1" in quotient
        for _ in quotient:
            if _ == '1':
                q_temp += 1
        # now we multiply q_temp by 2
        q = q_temp * 2
        # if odd is True, subtract 1 from q to get final q
        if odd == True:
            q = q - 1
            
        if remainder != '':
            r = int(remainder, 2)
        s = (q * m) + r

        decoded_data.append(s)
        length = f.read(1)

    temp = file.split(".")
    writefile = temp[0] + "_Dec.wav"  

    with wave.open(writefile, 'wb') as fd:
        fd.setparams(params)
        fd.writeframes(bytes(decoded_data))

    print("Decoding complete.")
    return writefile

## Compressing with K = 4 bits and the improved algorithm

In [31]:
sound1_encoded_improved, sound1_params = improved_encode("Exercise2_Files/Sound1.wav", 4)
sound1_decoded_improved = improved_decode(sound1_encoded_improved, 4, sound1_params)
get_info(sound1_decoded_improved)

Encoding complete.
Decoding complete.
Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (501022,)
Samples: [-7 -7 -7 ...  0  2  1]
<class 'numpy.ndarray'>


In [32]:
sound2_encoded_improved, sound2_params = improved_encode("Exercise2_Files/Sound2.wav", 4)
sound2_decoded_improved = improved_decode(sound2_encoded_improved, 4, sound2_params)
get_info(sound2_decoded_improved)

Encoding complete.
Decoding complete.
Sample rate: 44100
Channels: 1
Subtype: PCM_16
Shape: (504000,)
Samples: [ -999   886 -1325 ...    31  -876   339]
<class 'numpy.ndarray'>


<p style="font-size:15px;">The sizes of the encoded files using the improved algorithm are as follows:</p>
<table>
  <tr>
    <th>Sound File</th>
    <th>K</th>
    <th>Size of *.ex2 file</th>
  </tr>
  <tr>
    <td>Sound1.wav</td>
    <td>4</td>
    <td>2.5 MB</td>
  </tr>
  <tr>
    <td>Sound2.wav</td>
    <td>4</td>
    <td>2.55 MB</td>
  </tr>
</table>

## References
<ul>
    <li>
        https://www.coursera.org/learn/uol-cm3065-intelligent-signal-processing/ungradedLab/fh8wn/9-005-exercise-17-implementing-a-rice-encoder-and-decoder-using-python/lab 
    </li>
    <li>
        https://stackoverflow.com/questions/32675679/convert-binary-string-to-bytearray-in-python-3
    </li>
    <li>
        https://stackoverflow.com/questions/43787031/python-byte-array-to-bit-array
    </li>
    <li>
        https://stackoverflow.com/questions/24420820/how-to-write-on-new-string-uses-byte-wb-mode
    </li>
</ul>